In [1]:
!pip install datasets wandb note_seq soundfile jiwer pesq
!pip install -U huggingface_hub accelerate
!pip install --no-cache-dir transformers sentencepiece
!pip install --upgrade pyfluidsynth
!sudo apt install -y fluidsynth

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 13.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.4/209.4 kB 19.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 13.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 195.4/195.4 kB 10.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.5/258.5 kB 15.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 21.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.6/294.6 kB 26.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 25.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 5

In [2]:
from huggingface_hub import notebook_login
from datasets import load_dataset
import wandb
from argparse import Namespace

import torch
from transformers import AutoTokenizer, PreTrainedTokenizerFast, PreTrainedTokenizer, AutoConfig, \
                        GPT2LMHeadModel, DataCollatorForLanguageModeling, Trainer, TrainingArguments, \
                        LogitsProcessorList, LogitsProcessor

from tokenizers import Tokenizer
from tokenizers.models import WordLevel
from tokenizers.pre_tokenizers import WhitespaceSplit
from tokenizers.trainers import WordLevelTrainer

from IPython.display import Audio
import numpy as np

# The below two package imports would require a dedicated cell. With a function called token_to_note_seq
import note_seq

In [3]:
notebook_login()

In [4]:
wandb.login()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [ ]:
output_path = '/content/drive/MyDrive/MusicGPT/Final outputs'

In [ ]:
data_original = load_dataset('/content/drive/MyDrive/MusicGPT/test/original-chunked-tokens', split='train')['text'][0]
data_original

'PIECE_START TIME_SIGNATURE=4_4 GENRE=OTHER TRACK_START INST=0 DENSITY=4 BAR_START NOTE_ON=84 NOTE_ON=87 NOTE_ON=53 NOTE_ON=65 NOTE_ON=62 NOTE_ON=81 TIME_DELTA=0.5333333333333333 NOTE_ON=58 TIME_DELTA=0.26666666666666666 NOTE_ON=90 TIME_DELTA=0.2666666666666666 NOTE_OFF=84 NOTE_ON=72 TIME_DELTA=0.2666666666666666 NOTE_OFF=87 TIME_DELTA=0.8 NOTE_ON=64 TIME_DELTA=0.26666666666666666 NOTE_OFF=90 TIME_DELTA=0.26666666666666666 NOTE_ON=87 TIME_DELTA=0.26666666666666666 NOTE_OFF=64 TIME_DELTA=0.5333333333333333 NOTE_OFF=58 TIME_DELTA=0.5333333333333332 NOTE_ON=79 TIME_DELTA=0.2666666666666666 NOTE_OFF=53 NOTE_ON=41 NOTE_ON=60 TIME_DELTA=0.26666666666666666 NOTE_ON=83 NOTE_ON=88 NOTE_ON=53 TIME_DELTA=0.26666666666666666 NOTE_ON=75 TIME_DELTA=0.26666666666666666 NOTE_OFF=41 TIME_DELTA=0.2666666666666666 NOTE_OFF=65 NOTE_OFF=83 TIME_DELTA=0.2666666666666666 NOTE_OFF=62 NOTE_OFF=81 NOTE_OFF=88 NOTE_ON=41 NOTE_ON=65 TIME_DELTA=0.26666666666666666 NOTE_ON=69 TIME_DELTA=8.881784197001252e-16 NOTE_O

In [ ]:
data_generated = load_dataset('/content/drive/MyDrive/MusicGPT/test/generated-tokens', split='train')['text'][0]
data_generated

'PIECE_START TIME_SIGNATURE=4_4 GENRE=OTHER TRACK_START INST=0 DENSITY=4 BAR_START NOTE_ON=84 NOTE_ON=87 NOTE_ON=53 NOTE_ON=65 NOTE_ON=62 NOTE_ON=81 TIME_DELTA=0.5333333333333333 NOTE_ON=58 TIME_DELTA=0.26666666666666666 NOTE_ON=90 TIME_DELTA=0.2666666666666666 NOTE_OFF=84 NOTE_ON=72 TIME_DELTA=0.2666666666666666 NOTE_OFF=87 TIME_DELTA=0.8 NOTE_ON=64 TIME_DELTA=0.26666666666666666 NOTE_OFF=90 TIME_DELTA=0.26666666666666666 NOTE_ON=87 TIME_DELTA=0.26666666666666666 NOTE_OFF=64 TIME_DELTA=0.5333333333333333 NOTE_OFF=58 TIME_DELTA=0.5333333333333332 NOTE_ON=79 TIME_DELTA=0.2666666666666666 NOTE_OFF=53 NOTE_ON=41 NOTE_ON=60 TIME_DELTA=0.26666666666666666 NOTE_ON=83 NOTE_ON=88 NOTE_ON=53 TIME_DELTA=0.26666666666666666 NOTE_ON=75 TIME_DELTA=0.26666666666666666 NOTE_OFF=41 TIME_DELTA=0.2666666666666666 NOTE_OFF=65 NOTE_OFF=83 TIME_DELTA=0.2666666666666666 NOTE_OFF=62 NOTE_OFF=81 NOTE_OFF=88 NOTE_ON=41 NOTE_ON=65 TIME_DELTA=0.26666666666666666 NOTE_ON=69 TIME_DELTA=8.881784197001252e-16 NOTE_O

In [6]:
from IPython.display import Audio
import numpy as np
from pesq import pesq
import soundfile as sf

In [ ]:
original_numpy, original_float32 = convert_song_to_np(sample)
Audio(original_float32, rate=44100)

In [ ]:
generated_song_text, generated_numpy, gen_float32 = generate_song_sequence("PIECE_START TIME_SIGNATURE=3_4 GENRE=OTHER TRACK_START INST=41 DENSITY=2 BAR_START TIME_DELTA=2.0 NOTE_ON=55 TIME_DELTA=4.0 NOTE_OFF=55 NOTE_ON=55 TIME_DELTA=4.0 NOTE_OFF=55 NOTE_ON=55 TIME_DELTA=2.0 NOTE_OFF=55 BAR_END BAR_START TIME_DELTA=2.0 NOTE_ON=57 TIME_DELTA=4.0 NOTE_OFF=57 NOTE_ON=60 TIME_DELTA=4.0 NOTE_OFF=60 NOTE_ON=60")
Audio(gen_float32, rate=44100)

In [7]:
def save_song_as_wav(int16_array, name="sample", sr=16000):
  # Convert the int16 array back to float32 for saving
  float32_array = int16_array.astype(np.float32) / np.iinfo(np.int16).max

  # Specify the path and filename for the output audio file
  output_audio_path = f'/content/drive/MyDrive/MusicGPT/{name}.wav'

  # Save the float32 array as a WAV file
  sf.write(output_audio_path, float32_array, SAMPLE_RATE)

  print(f"Audio saved to {output_audio_path}")

In [ ]:
save_song_as_wav(original_numpy)

Audio saved to /content/drive/MyDrive/MusicGPT/sample.wav


In [ ]:
save_song_as_wav(generated_numpy, "generated_sample")

Audio saved to /content/drive/MyDrive/MusicGPT/generated_sample.wav


In [11]:
ref, rate = sf.read('/content/drive/MyDrive/MusicGPT/test/0_original.wav')
deg, rate = sf.read('/content/drive/MyDrive/MusicGPT/test/0_cont.wav')

pesq_score = pesq(rate, ref, deg, 'wb')  # 'wb' for wideband, 'nb' for narrowband
print("PESQ Score:", pesq_score)
print(rate, ref)
print(rate, deg)

PESQ Score: 1.3387936353683472
16000 [-0.1723938  -0.17236328 -0.16500854 ... -0.15640259 -0.15634155
 -0.14041138]
16000 [-0.17663574 -0.17660522 -0.16903687 ... -0.12231445 -0.11712646
 -0.10321045]


In [ ]:
import librosa as lb

resampled_data_original = lb.resample(original_float32, orig_sr=44100, target_sr=16000)

array([-0.12588635,  0.15371907, -0.1662826 , ...,  2.2058454 ,
       -0.76318526, -1.5254025 ], dtype=float32)

In [ ]:
resampled_data_original.astype(np.float32)

array([-0.12588635,  0.15371907, -0.1662826 , ...,  2.2058454 ,
       -0.76318526, -1.5254025 ], dtype=float32)

In [ ]:
resampled_data_generated = lb.resample(gen_float32, orig_sr=44100, target_sr=16000)
resampled_data_generated

array([ 0.        ,  0.        ,  0.        , ..., -0.1252567 ,
       -0.03066541,  0.11490464], dtype=float32)

In [ ]:
print("PESQ: ", pesq(16000, resampled_data_generated, resampled_data_original, 'wb'))

PESQ:  2.255187511444092


In [ ]:
from jiwer import wer, cer

sample_song = data_original
generated_song = data_generated


In [ ]:
"Word Error Rate: ", wer(sample_song, generated_song)

('Word Error Rate: ', 0.8594507269789984)

In [ ]:
"Character Error Rate: ", cer(sample_song, generated_song)

('Character Error Rate: ', 0.4948394495412844)